In [1]:
import pandas as pd
import tarfile
import csv

tar = tarfile.open("/Users/gavincleach/Desktop/famous-chord-progressions-raw-data/billboard-2.0-salami_chords.tar.gz", "r:gz")
famous_chord_progressions_coded = []
for member in tar.getmembers():
    f = tar.extractfile(member)
    famous_chord_progressions_coded.append(f.read())


famous_chord_progressions = []

for song in famous_chord_progressions_coded:
    famous_chord_progressions.append(song.decode("utf-8"))
    
    

billboard_charts = pd.read_csv('/Users/gavincleach/Desktop/famous-chord-progressions-raw-data/billboard-2.0-index.csv')
        
len(famous_chord_progressions)

890

In [2]:
billboard_charts.set_index("id", inplace = True)

billboard_charts.head()

chart_date  target_rank  actual_rank                title  \
id                                                              
1   1987-07-11           82          NaN                  NaN   
2   1973-08-04           14          NaN                  NaN   
3   1961-07-03           56         57.0         I Don't Mind   
4   1971-08-07           32         31.0  You've Got A Friend   
5   1976-07-10           51          NaN                  NaN   

                          artist  peak_rank  weeks_on_chart  
id                                                           
1                            NaN        NaN             NaN  
2                            NaN        NaN             NaN  
3                    James Brown       47.0             8.0  
4   Roberta Flack,Donny Hathaway       29.0            12.0  
5                            NaN        NaN             NaN

let's first get rid of the rows in `billboard_charts` that have `NaN` value in the `title` column. There are 890 songs with full chord progressions, so we will see how many entries we have in `billboard_charts` after we drop those rows.

In [3]:
unwanted_portion = billboard_charts.loc[billboard_charts['title'].isnull()]
ids_to_drop = list(unwanted_portion.index) 

billboard_charts = billboard_charts.drop(labels = ids_to_drop, axis = 0)

billboard_charts.shape

(890, 7)

Great! So now we only have the remaining song entries that don't have `NaN` entries.

Before we clean up `billboard_charts`, we should clean up the `famous_chord_progressions` list, because there is much more work to do on that.

It would be beneficial to understand what each item in the list `famous_chord_progressions` means. So...

(ignore \'s)

\# title: \
after this comes the title of the song. 

\# artist: \
after this comes the artist name.

\# metre: \
after this comes the time signature.

\# tonic: \
after this comes the key the song starts in. 

for tonic and metre there my not be a definite answer for each of these, in that case, there will be a '?' in place. Tonic and metre might change throughout the song as well.

In [4]:
songs = pd.DataFrame(columns = ['Title', 'Artist', 'Metres', 'Keys', 'Part_1_name', 'Part_1_Progression', 'Part_1_Repetitions', 'Part_2_name', 'Part_2_Progression', 'Part_2_Repetitions', 'Part_3_name', 'Part_3_Progression', 'Part_3_Repetitions', 'Part_4_name', 'Part_4_Progression', 'Part_4_Repetitions', 'Part_5_name', 'Part_5_Progression', 'Part_5_Repetitions', 'Part_6_name', 'Part_6_Progression', 'Part_6_Repetitions', 'Part_7_name', 'Part_7_Progression', 'Part_7_Repetitions', 'Part_8_name', 'Part_8_Progression', 'Part_8_Repetitions', 'Part_9_name', 'Part_9_Progression', 'Part_9_Repetitions', 'Part_10_name', 'Part_10_Progression', 'Part_10_Repetitions', 'Part_11_name', 'Part_11_Progression', 'Part_11_Repetitions', 'Part_12_name', 'Part_12_Progression', 'Part_12_Repetitions', 'Part_13_name', 'Part_13_Progression', 'Part_13_Repetitions', 'Part_14_name', 'Part_14_Progression', 'Part_14_Repetitions', 'Part_15_name', 'Part_15_Progression', 'Part_15_Repetitions', 'Part_16_name', 'Part_16_Progression', 'Part_16_Repetitions', 'Part_17_name', 'Part_17_Progression', 'Part_17_Repetitions', 'Part_18_name', 'Part_18_Progression', 'Part_18_Repetitions', 'Part_19_name', 'Part_19_Progression', 'Part_19_Repetitions', 'Part_20_name', 'Part_20_Progression', 'Part_20_Repetitions', 'Part_21_name', 'Part_21_Progression', 'Part_21_Repetitions', 'Part_22_name', 'Part_22_Progression', 'Part_22_Repetitions', 'Part_23_name', 'Part_23_Progression', 'Part_23_Repetitions', 'Part_24_name', 'Part_24_Progression', 'Part_24_Repetitions', 'Part_25_name', 'Part_25_Progression', 'Part_25_Repetitions', 'Part_26_name', 'Part_26_Progression', 'Part_26_Repetitions'])

In [5]:
import re
import sys

most_song_parts = 0
for i in range(0, 890):
    
    song_example = famous_chord_progressions[i]
    part_of_song_example = "# title: I Don't mind\n# artist: Jam"

    title_part_of_song_example = song_example.split(' title: ')[1]
    title_pattern = "(.+)\n"
    
    #Out Of Sight, Out Of Mind     has comma in title. Messes up the rest of the stuff
    #Dirty Water      has commas in some of the chords like D:sus4(b7,9)
    title_comma = False
    
    artist_part_of_song_example = song_example.split(' artist: ')[1]
    
    artist_pattern = "(.+)\n"

    metre_part_of_song_example = song_example.split(' metre: ')[1]
    
    metre_pattern = "([0-9]/[0-9])\n"
    
    tonic_part_of_song_example = song_example.split(' tonic: ')[1]
    
    #print('does the metre ever change?????')
    #if len(re.findall('metre:', song_example)) > 1:
        #print('the tempo changed in this song')
        #sys.exit('tempo changed')
    
    
    #key changes in 'Paradise by the Dashboard Light'
    # D:maj |\n# tonic: Bb\n437.987188208\tG, key change, | Eb:maj |
    
    #tempo changes in 'Is That All There Is'
    #| Bb:maj | N |\n# metre: 4/4\n35.805170068\tB, chorus, | G:13 | G:13 
    
    
    tonic_pattern = "([ABCDEFG]b?#?)\n"
    
    comma_split_list = re.split(', ', song_example)[1:]
    refined_comma_split_list = []
    
    for portion in comma_split_list:
        if re.match("\([a-z]+", portion):
            refined_comma_split_list.append(refined_comma_split_list[-1] + ' ' + portion)
            refined_comma_split_list.pop(-2)
        elif re.match("[a-z]+\)", portion):
            refined_comma_split_list.append(refined_comma_split_list[-1] + ' ' + portion)
            refined_comma_split_list.pop(-2)
        else:
            refined_comma_split_list.append(portion)
    print(song_example)
    print('\n\n\n')
    print(refined_comma_split_list)  
    print('\n\n\n')
        
    comma_split_list_len = len(refined_comma_split_list)     
    if (comma_split_list_len / 2) > most_song_parts:
        most_song_parts = comma_split_list_len / 2


  
    
    title_result = re.findall(title_pattern, title_part_of_song_example)[0]
    artist_result = re.findall(artist_pattern, artist_part_of_song_example)[0]
    metre_results = re.findall(metre_pattern, metre_part_of_song_example)       
    tonic_results = re.findall(tonic_pattern, tonic_part_of_song_example)
    
    comma_in_artist_title = 0
    if "," in title_result:
        comma_in_artist_title += 1
    if "," in artist_result:
        comma_in_artist_title += 1
    
    #WE HAVE TO ACCOMODATE SO THAT SONGS CAN HAVE UP TO 23 PARTS AS FAR AS WE KNOW SO FAR
    
    chords_pattern = "([ABCDEFG][#b]?\S+) \|?"
    
    #maybe the part will repeat itself!
    repetition_pattern = "x(\d+)"
    
    parts_result_chords_repeat = []
    previous_part = []
    for part_number in range(1, 24):
        #PART RESULT
        
        if comma_split_list_len >= (comma_in_artist_title + 2*part_number):
            part_result = refined_comma_split_list[comma_in_artist_title + 2*part_number -2]
            part_of_song_chords = refined_comma_split_list[comma_in_artist_title + 2*part_number -1]
            part_chords_result = re.findall(chords_pattern, part_of_song_chords)
        
        if len(re.findall(repetition_pattern, part_of_song_chords)) == 0:
            part_repeat_result = 1
        else:
            part_repeat_result = re.findall(repetition_pattern, part_of_song_chords)[0]
        if [part_result, part_chords_result, part_repeat_result] == previous_part:
            break
        previous_part = [part_result, part_chords_result, part_repeat_result]
        parts_result_chords_repeat.append(previous_part)
    
    #test
    print('This is your test')
    print(parts_result_chords_repeat)
    print('\n\nTHISTESTISOVER\n')
    #test over
    def return_with_added_empties():
        if len(parts_result_chords_repeat) < 26:
            parts_result_chords_repeat.append(['empty', 'empty', 'empty'])
            return_with_added_empties()
    return_with_added_empties()
    print(parts_result_chords_repeat)  
    print(parts_result_chords_repeat[23][1])
    
  
    print(title_result)
    print(artist_result)
    print(metre_results)
    print(tonic_results)
    
    row_series = pd.Series([title_result, artist_result, metre_results, tonic_results, parts_result_chords_repeat[0][0], parts_result_chords_repeat[0][1], parts_result_chords_repeat[0][2], parts_result_chords_repeat[1][0], parts_result_chords_repeat[1][1], parts_result_chords_repeat[1][2], parts_result_chords_repeat[2][0], parts_result_chords_repeat[2][1], parts_result_chords_repeat[2][2], parts_result_chords_repeat[3][0], parts_result_chords_repeat[3][1], parts_result_chords_repeat[3][2], parts_result_chords_repeat[4][0], parts_result_chords_repeat[4][1], parts_result_chords_repeat[4][2], parts_result_chords_repeat[5][0], parts_result_chords_repeat[5][1], parts_result_chords_repeat[5][2], parts_result_chords_repeat[6][0], parts_result_chords_repeat[6][1], parts_result_chords_repeat[6][2], parts_result_chords_repeat[7][0], parts_result_chords_repeat[7][1], parts_result_chords_repeat[7][2], parts_result_chords_repeat[8][0], parts_result_chords_repeat[8][1], parts_result_chords_repeat[8][2], parts_result_chords_repeat[9][0], parts_result_chords_repeat[9][1], parts_result_chords_repeat[9][2], parts_result_chords_repeat[10][0], parts_result_chords_repeat[10][1], parts_result_chords_repeat[10][2], parts_result_chords_repeat[11][0], parts_result_chords_repeat[11][1], parts_result_chords_repeat[11][2], parts_result_chords_repeat[12][0], parts_result_chords_repeat[12][1], parts_result_chords_repeat[12][2], parts_result_chords_repeat[13][0], parts_result_chords_repeat[13][1], parts_result_chords_repeat[13][2], parts_result_chords_repeat[14][0], parts_result_chords_repeat[14][1], parts_result_chords_repeat[14][2], parts_result_chords_repeat[15][0], parts_result_chords_repeat[15][1], parts_result_chords_repeat[15][2], parts_result_chords_repeat[16][0], parts_result_chords_repeat[16][1], parts_result_chords_repeat[16][2], parts_result_chords_repeat[17][0], parts_result_chords_repeat[17][1], parts_result_chords_repeat[17][2], parts_result_chords_repeat[18][0], parts_result_chords_repeat[18][1], parts_result_chords_repeat[18][2], parts_result_chords_repeat[19][0], parts_result_chords_repeat[19][1], parts_result_chords_repeat[19][2], parts_result_chords_repeat[20][0], parts_result_chords_repeat[20][1], parts_result_chords_repeat[20][2], parts_result_chords_repeat[21][0], parts_result_chords_repeat[21][1], parts_result_chords_repeat[21][2], parts_result_chords_repeat[22][0], parts_result_chords_repeat[22][1], parts_result_chords_repeat[22][2], parts_result_chords_repeat[23][0], parts_result_chords_repeat[23][1], parts_result_chords_repeat[23][2], parts_result_chords_repeat[24][0], parts_result_chords_repeat[24][1], parts_result_chords_repeat[24][2], parts_result_chords_repeat[25][0], parts_result_chords_repeat[25][1], parts_result_chords_repeat[25][2]])
    row_df = pd.DataFrame([row_series])

    songs = pd.concat([songs, row_df])
    
    

    for entries in parts_result_chords_repeat:
        for entry in entries:
            print(entry)
    
    print("the most parts in a song is {}".format(most_song_parts))


# title: I Don't mind
# artist: James Brown
# metre: 6/8
# tonic: C

0.0	silence
7.3469387e-2	A, intro, | A:min | A:min | C:maj | C:maj |
8.714013605	| A:min | A:min | C:maj | C:maj |
15.611995464	| A:min | A:min | C:maj | C:maj |
22.346394557	B, verse, | A:min | A:min | C:maj | C:maj |, (voice
29.219433106	| A:min | A:min | C:maj | C:maj |
36.279501133	| F:maj | F:maj | D:maj | D:maj |
43.053922902	| G:maj | G:maj | C:maj | C:maj |
49.23802721	B, verse, | A:maj | A:maj | C:maj | C:maj |
56.185079365	| A:maj | A:maj | C:maj | C:maj |
63.007732426	| F:maj | F:maj | D:maj | D:maj |
69.942857142	| G:maj | G:maj | C:maj | C:maj |, voice)
76.123990929	A, interlude, | A:min | A:min | C:maj | C:maj |
82.811201814	| A:min | A:min | C:maj | C:maj |
89.535532879	| F:maj | F:maj | D:maj | D:maj |
96.418956916	| G:maj | G:maj | C:maj | C:maj |, (guitar)
102.924353741	B, verse, | A:maj | A:maj | C:maj | C:maj |, (voice
109.886984126	| A:maj | A:maj | C:maj | C:maj |
116.791473922	| F:maj | F:maj | 

intro
['A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min']
1
verse
['A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'F:maj', 'F:maj', 'G:maj', 'G:maj', 'A:min', 'A:min', 'A:min', 'A:min']
1
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
the most parts in a song is 14.0
# title: Kiss On My List
# artist: Hall & Oates
# metre: 4/4
# tonic: C

0.0	silence
0.442630385	A, intro, | C:maj G:maj/11 | A:min/b3 G:maj/11 | C:min7 | C:min7 | F:maj | F:maj | C:maj | C:maj |, (keyboard) 
17.080816326	B, verse, | C:min | C:min | F:min | F:min | Ab:maj | Bb:maj | C:maj(9) | C:maj(

intro
['E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj']
1
verse
['E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj']
1
pre-chorus
['Bb:maj', 'F:maj', 'C:maj', 'F:maj', 'Bb:maj', 'C:maj', 'F:maj', 'Bb:maj', 'F:maj', 'C:maj', 'F:maj', 'Bb:maj', 'G:maj', 'C:maj']
1
chorus
['E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj']
1
trans
['E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj']
1
verse
['E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj', 'E:maj', 'A:maj', 'E:maj']
1
pre-chorus
['Bb:maj', 'F:maj', 'C:maj', 'F:maj', 'Bb:maj', 'C:maj', 'F:maj', 'Bb:maj', 'F:maj', 'C:maj', 'F:maj', 'Bb:maj', 'G:maj', 'C:maj']
1
chorus
['E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj', 'E:maj', 'A:maj', 'D:maj', 'A:maj']
1
bridge
['B:min', 'B:min', 'G:maj', 'G:maj', 

intro
['G:min', 'G:min', 'A:min', 'D:min', 'D:min', 'A:min', 'G:maj', 'A:min', 'Bb:maj', 'F:maj', 'F:maj']
1
verse
['C:maj', 'F:min/5', 'C:maj', 'G:maj/11', 'F:maj/5', 'F:min/5', 'C:maj', 'F:min/5', 'C:maj', 'G:maj/11', 'F:maj/5', 'G:maj/11']
1
pre-chorus
['F:maj', 'D:min', 'F:maj', 'D:min', 'G:sus4']
1
chorus
['A:min', 'G:maj', 'E:min', 'A:min']
2
transition
['G:min', 'G:min', 'A:min', 'D:min', 'D:min', 'A:min', 'G:maj', 'A:min', 'Bb:maj', 'F:maj', 'F:maj', 'F:maj']
1
verse
['C:maj', 'F:min/5', 'C:maj', 'G:maj/11', 'F:maj/5', 'F:min/5', 'C:maj']
1
pre-chorus
['F:maj', 'D:min', 'F:maj', 'D:maj', 'F:maj', 'D:min', 'G:sus4']
1
chorus
['A:min', 'G:maj', 'E:min', 'A:min']
2
interlude
['D:min', 'A:min', 'G:maj', 'A:min', 'Bb:maj', 'F:maj', 'F:maj', 'F:maj']
1
outro
['A:min', 'G:maj', 'E:min', 'A:min']
4
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empt

intro
['D:1', 'D:1', 'D:1', 'D:1', 'D:1', 'D:1', 'D:1', 'D:1']
1
bass guitar)
31.904058956	B
[]
1
| E:min | E:min | E:min | E:min | (voice
39.685124716	| E:min | E:min | E:min | E:min |
47.355351473	| E:min | E:min | E:min | E:min |
55.011746031	| E:min | E:min | E:min | E:min |
62.60292517	C
[]
1
| C:maj | D:maj | E:min | E:min |
70.277256235	| C:maj | D:maj | E:min | E:min |
77.912517006	D
[]
1
| E:min | C:maj D:sus4 | E:min | C:maj D:sus4 |
85.613809523	| E:min | C:maj D:sus4 | E:min | C:maj D:sus4 |
93.282607709	| E:min | C:maj D:sus4 | E:min | C:maj D:sus4 |
100.899206349	| E:min | C:maj D:sus4 | E:min | C:maj D:sus4 |
108.536417233	B
[]
1
| E:min | E:min | E:min | E:min |
116.207256235	| E:min | E:min | E:min | E:min |
123.853832199	| E:min | E:min | E:min | E:min |
131.532426303	| E:min | E:min | E:min | E:min |
139.197460317	C
[]
1
| C:maj | D:maj | E:min | E:min |
146.846780045	| C:maj | D:maj | E:min | E:min |
154.474263038	D
[]
1
| E:min | C:maj D:sus4 | E:min | C:maj D:sus4

...

intro
['A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min']
1
verse
['A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'A:min', 'F:maj', 'F:maj', 'G:maj', 'G:maj', 'A:min', 'A:min', 'A:min', 'A:min']
1
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
the most parts in a song is 26.0
# title: Baby Don t Forget My Number
# artist: Milli Vanilli
# metre: 4/4
# tonic: Ab

0.0	silence
0.232199546	A, intro, | Ab:1(b7) | Ab:1(b7) | Ab:1(b7) | Ab:1(b7) | Db:1(b7) |
12.133174603	B, interlude, | Ab:1(b7) | Ab:1(b7) Db:1(b7) . . | Gb:1(b7) | Ab:1(b7) . . Gb:1(b7) |, (synthesizer
21.7149886

intro
['F#:maj', 'A:maj', 'B:maj', 'F#:maj', 'F#:maj', 'A:maj', 'B:maj', 'F#:maj']
1
verse
['F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
chorus
['A:maj', 'B:min', 'A:maj', 'B:min', 'A:maj', 'B:min', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
verse
['F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
chorus
['A:maj', 'B:min', 'A:maj', 'B:min', 'A:maj', 'B:min', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
bridge
['F#:maj', 'A:maj', 'B:maj', 'F#:maj', 'F#:maj', 'A:maj', 'B:maj', 'F#:maj', 'F#:maj', 'A:maj', 'B:maj', 'F#:maj', 'F#:maj', 'A:maj', 'B:maj', 'F#:maj']
1
verse
['F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
chorus
['A:maj', 'B:min', 'A:maj', 'B:min', 'A:maj', 'B:min', 'F#:maj', 'F#:maj', 'F#:maj', 'F#:maj']
1
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
em

intro
['G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7']
1
chorus
['G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7']
1
verse
['G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'Ab:min']
1
bridge
['Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7']
1
verse
['G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'Ab:min']
1
bridge
['Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7']
1
verse
['G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'C:maj', 'F:maj', 'G:min7', 'Bb:maj', 'C:maj', 'F:maj', 'G:min7', 'G:min7', 'Ab:min']
1
bridge
['Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:min7', 'Bb:m

intro
['F#:min', 'F#:min', 'F#:min', 'F#:min']
1
verse
['F#:min', 'F#:min', 'E:maj', 'E:maj', 'D:7', 'D:7', 'C#:7', 'C#:7']
1
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
the most parts in a song is 26.0
# title: He's So Fine
# artist: The Chiffons
# metre: 4/4
# tonic: G

0.0	silence
0.394739229	A', intro, | A:min7 | D:maj | A:min7 | D:maj |
6.780226757	A, verse, | A:min7 | D:maj | A:min7 | D:maj |, (voice
13.531519274	| A:min7 | D:maj | A:min7 | D:maj |
20.178231292	| G:maj | G:maj | G:maj | G:maj |
26.799455782	| G:maj | G:maj | G:maj | G:maj |
33.483174603	A, verse, | A:min7 | D:maj | A:min7 | D:maj |


intro
['C:min7', 'Bb:maj', 'C:min7', 'Bb:maj']
1
verse
['Bb:maj', 'Bb:7', 'Bb:maj', 'Bb:7', 'Bb:maj', 'Bb:7', 'Eb:maj', 'Eb:maj', 'G:min', 'G:min', 'F:maj', 'F:maj', 'Ab:maj(9)', 'Ab:maj(9)', 'Ab:maj(9)', 'Ab:maj(9)']
1
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
empty
the most parts in a song is 26.0


In [6]:
songs.head()


0                                 1      2     3      4  \
0         I Don't mind                       James Brown  [6/8]   [C]  intro   
0  You've got a Friend  Roberta Flack and Donny Hathaway  [4/4]  [Ab]  intro   
0             The Rose                      Bette Midler  [4/4]   [C]  intro   
0      An Innocent Man                        Billy Joel  [4/4]   [C]  intro   
0    Lookin' for Love                         Johnny Lee  [4/4]   [D]  intro   

                                                   5  6      7  \
0  [A:min, A:min, C:maj, C:maj, A:min, A:min, C:m...  1  verse   
0           [Ab:maj, Db:maj/5, Ab:maj, G:hdim7, C:7]  1  verse   
0                                              [C:5]  4  verse   
0                                            [C:maj]  4  verse   
0  [E:min, F#:min, G:maj, A:maj, E:min, F#:min, G...  1  verse   

                                                   8  9  ...  \
0  [A:min, A:min, C:maj, C:maj, A:min, A:min, C:m...  1  ...   
0  [F:min, C:7/5, C:7, F:min, C:7/5, F:min/b3, C:...  1  ...   
0  [C:maj, G:maj/3, F:maj/3, G:maj/3, C:maj, C:ma...  1  ...   
0  [C:maj, C:maj, D:min, D:min, F:maj, G:maj, G:m...  1  ...   
0  [G:maj, G:maj, D:maj, D:maj, G:maj, D:maj, A:m...  1  ...   

  Part_7_Progression Part_7_Repetitions Part_7_name Part_8_Progression  \
0                NaN                NaN         NaN                NaN   
0                NaN                NaN         NaN                NaN   
0                NaN                NaN         NaN                NaN   
0                NaN                NaN         NaN                NaN   
0                NaN                NaN         NaN                NaN   

  Part_8_Repetitions Part_8_name Part_9_Progression Part_9_Repetitions  \
0                NaN         NaN                NaN                NaN   
0                NaN         NaN                NaN                NaN   
0                NaN         NaN                NaN                NaN   
0                NaN         NaN                NaN                NaN   
0                NaN         NaN                NaN                NaN   

  Part_9_name Title  
0         NaN   NaN  
0         NaN   NaN  
0         NaN   NaN  
0         NaN   NaN  
0         NaN   NaN  

[5 rows x 164 columns]

What we want to do is be able to analyze each song and categorize it into different modal tendencies, as well as by the numerical music system, i.e 1, 2, 3, 4, 5, 6, 7, 8 tones in the key. 

A good way to start this is to look at the key of C. For each mode we will look at the different scales corresponding to the key.

FOR THE KEY "C"

Ionian/Major Scale: CM, Dm, Em, FM, GM, Am, Bdim

Dorian: Cm, Dm, EbM, FM, Gm, Adim, BbM

Phrygian: Cm, DbM, EbM, Fm, Gdim, AbM, Bbm

Lydian: CM, DM, Em, F#dim, GM, Am, Bm

Mixolydian: CM, Dm, Edim, FM, Gm, Am, BbM

Aeolian: Cm, Ddim, EbM, Fm, Gm, AbM, BbM

Locrian: Cdim, DbM, Ebm, Fm, GbM, AbM, Bbm

Let's take the first song in our dataset as an example...

In [7]:

#find which columns we need (how many parts the song has)
songs.iloc[[0], [4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24]]

4                                                  5  6      7   \
0  intro  [A:min, A:min, C:maj, C:maj, A:min, A:min, C:m...  1  verse   

                                                  8  9      10  \
0  [A:min, A:min, C:maj, C:maj, A:min, A:min, C:m...  1  verse   

                                                  11 12         13  ... 15  \
0  [A:maj, A:maj, C:maj, C:maj, A:maj, A:maj, C:m...  1  interlude  ...  1   

      16                                                 17 18         19  \
0  verse  [A:maj, A:maj, C:maj, C:maj, A:maj, A:maj, C:m...  1  interlude   

                                                  20 21     22     23     24  
0  [A:min, A:min, C:maj, C:maj, A:min, A:min, C:m...  1  empty  empty  empty  

[1 rows x 21 columns]

In [8]:
#I Don't Mind


print('INTRO')
print(songs.iat[0, 5])
print('\n')

print('VERSE')
print(songs.iat[0, 8])
print('\n')

print('VERSE')
print(songs.iat[0, 11])
print('\n')

print('INTERLUDE')
print(songs.iat[0, 14])
print('\n')

print('VERSE')
print(songs.iat[0, 17])
print('\n')

print('INTERLUDE')
print(songs.iat[0, 20])
print('\n')

INTRO
['A:min', 'A:min', 'C:maj', 'C:maj', 'A:min', 'A:min', 'C:maj', 'C:maj', 'A:min', 'A:min', 'C:maj', 'C:maj']


VERSE
['A:min', 'A:min', 'C:maj', 'C:maj', 'A:min', 'A:min', 'C:maj', 'C:maj', 'F:maj', 'F:maj', 'D:maj', 'D:maj', 'G:maj', 'G:maj', 'C:maj', 'C:maj']


VERSE
['A:maj', 'A:maj', 'C:maj', 'C:maj', 'A:maj', 'A:maj', 'C:maj', 'C:maj', 'F:maj', 'F:maj', 'D:maj', 'D:maj', 'G:maj', 'G:maj', 'C:maj', 'C:maj']


INTERLUDE
['A:min', 'A:min', 'C:maj', 'C:maj', 'A:min', 'A:min', 'C:maj', 'C:maj', 'F:maj', 'F:maj', 'D:maj', 'D:maj', 'G:maj', 'G:maj', 'C:maj', 'C:maj']


VERSE
['A:maj', 'A:maj', 'C:maj', 'C:maj', 'A:maj', 'A:maj', 'C:maj', 'C:maj', 'F:maj', 'F:maj', 'D:maj', 'D:maj', 'G:maj', 'G:maj', 'C:maj', 'C:maj']


INTERLUDE
['A:min', 'A:min', 'C:maj', 'C:maj', 'A:min', 'A:min', 'C:maj', 'C:maj', 'A:min']




What we eventually want to accomplish is for each song create a visualization showing the key/s and the mode/s of each song along with their tendencies towards other keys and modes. Also, we want to create a mapping of each song based on the numerical chord progressions.

To effectively do all of this, we want to create a note composition of each chord that is present in this whole database.

In [9]:
unique_chords = []
prog_columns = [5, 8, 11, 14, 17, 20, 23, 26]
for index, row in songs.iterrows():
    for col_num in prog_columns:
        for chord in row[col_num]:
            if chord not in unique_chords:
                unique_chords.append(chord)
unique_chords.remove('e')
unique_chords.remove('m')
unique_chords.remove('p')
unique_chords.remove('t')
unique_chords.remove('y')
print(unique_chords)
    

['A:min', 'C:maj', 'F:maj', 'D:maj', 'G:maj', 'A:maj', 'Ab:maj', 'Db:maj/5', 'G:hdim7', 'C:7', 'F:min', 'C:7/5', 'F:min/b3', 'Bb:min7', 'Eb:7', 'C:min7', 'Eb:11', 'Eb:maj', 'Ab:7', 'Db:maj', 'Ab:maj7', 'Gb:maj', 'Db:maj7', 'Gb:maj(9)', 'Gb:7', 'F:min7', 'C:5', 'G:maj/3', 'F:maj/3', 'C:maj/7', 'F:sus2/3', 'F:maj/9', 'G:7', 'C:maj(9)', 'G:maj(9)', 'F:maj(9)', 'E:min/5', 'A:min(11)', 'A:maj(11)/b7', 'E:min', 'D:min', 'G:min7', 'C:maj/5', 'Bb:maj/5', 'F:maj/5', 'D:min7', 'C:maj/3', 'F#:min', 'A:maj/b7', 'A:maj/13', 'A:maj/5', 'F#:maj', 'A:maj6', 'Db:min(9)', 'Gb:maj6(b7)', 'Eb:7(#9)', 'G:maj/11', 'A:min/b3', 'C:min', 'Bb:maj', 'F:sus2', 'G:min7/5', 'F:min9', 'Bb:min', 'Eb:min', 'Gb:maj6', 'Gb:maj/5', 'Gb:maj/9', 'Bb:min/b7', 'Db:7', 'G:maj/5', 'B:min', 'D#:dim', 'D:maj/3', 'G:maj7', 'C:maj7', 'B:sus4(b7,9)', 'B:7', 'E:min7', 'A:sus4(b7)', 'A:7', 'C:maj6', 'D:maj/b7', 'D:maj7', 'E:maj/3', 'C#:sus4(b7,9)', 'C#:7', 'F#:min7', 'B:sus4(b7)', 'E:maj', 'D:maj6', 'C#:min7', 'D:maj13', 'D:min/5', '

We want to extract all of the possible types of chords. We will do this by splitting each of these elements by ':' and take the right-hand side of the split.

In [10]:
unique_chord_types = []
for chord in unique_chords:
    chord_type = chord.split(':')[1]
    if chord_type not in unique_chord_types:
        unique_chord_types.append(chord_type)
    

print(unique_chord_types)

['min', 'maj', 'maj/5', 'hdim7', '7', '7/5', 'min/b3', 'min7', '11', 'maj7', 'maj(9)', '5', 'maj/3', 'maj/7', 'sus2/3', 'maj/9', 'min/5', 'min(11)', 'maj(11)/b7', 'maj/b7', 'maj/13', 'maj6', 'min(9)', 'maj6(b7)', '7(#9)', 'maj/11', 'sus2', 'min7/5', 'min9', 'min/b7', 'dim', 'sus4(b7,9)', 'sus4(b7)', 'maj13', 'sus4', 'dim/b5', '1', 'min/11', 'sus2(b7)', 'maj9', 'minmaj7', 'aug(b7)', '9', 'min7/b7', 'maj6/3', 'maj7/5', '13', 'sus2/9', '5/13', 'maj/b3', '9(b13)', 'aug', '1(b5,b7,3)/b5', 'sus4/5', 'min7(11)', 'sus4/11', '7/3', 'min/13', '9/5', '9(13,#11)', 'min9/9', '1(11,9)', 'maj7/9', '5(b7)', 'maj6(b7,11)', '5(13)', 'min7/11', 'maj6(9)', 'min11/b3', '7(b9)', 'dim7/b3', '1(b3,b7,11,9)', 'sus4(b7,9,13)', 'min6/5', '1(#5)', 'min6', 'maj6(9)/5', 'min9/5', 'min/7', 'dim7', 'min/b1', 'maj6/13', 'maj(9)/3', 'aug(b7,9)', '1(b5,b7,3)', '1(b7)/b7', '1(13)/13', '1(3)', 'min/3', 'maj7/7', 'sus4(b7)/9', 'hdim7/b3', '7/11', 'dim/b3', 'maj(b9)', 'sus4(9)', 'maj6(7)', '7/b7', '7(#11)', 'maj(11)', 'maj/

Now for each of these chord types, we will break them down into their components numerically...

In [11]:
import re
all_notes = ['C', 'Db', 'D', 'Eb', 'E', 'F', 'Gb', 'G', 'Ab', 'A', 'Bb', 'B']
#            1,   , 2,   , 3, 4,   , 5,   , 6,   , 7

#All numbers will reference the Major Ionian scale.
#1(...) represents unharmonized bass notes with other notes in parentheses
#.../x represents an inversion
#bassiest notes come first in list
#all numbers are mod7, i.e '2' represents the same note (maybe different pitch/octave) as '9'
#chords with / followed by tone not present will be interpreted as that chord adding what is after the '/', inverted to the tone after the slash.
#parentheses with more than one component will assume bassier notes come first
#unique_chord_types_disassembled = {'min': ['1', 'b3', '5'], 'maj': ['1', '3', '5'], 'maj/5': ['5', '1', '3'], 'hdim7': ['1', 'b3', 'b5', 'b7'], '7': ['1', '3', '5', 'b7'], '7/5': ['5', 'b7', '1', '3'], 'min/b3': ['b3', '5', '1'], 'min7': ['1', 'b3', '5', 'b7'], '11': ['1', '3', '5', 'b7', '9', '11'], 'maj7': ['1', '3', '5', '7'], 'maj(9)': ['1', '3', '5', '9'], '5': ['1', '5'], 'maj/3': ['3', '5', '1'], 'maj/7': ['7', '1', '3', '5'], 'sus2/3': ['3', '5', '1', '2'], 'maj/9': ['9', '1', '3', '5'], 'min/5': ['5', '1', 'b3'], 'min(11)': ['1', 'b3', '5', '11'], 'maj(11)/b7': ['b7', '11', '1', '3', '5'], 'maj/b7': ['b7', '1', '3', '5'], 'maj/13': ['13', '1', '3', '5'], 'maj6': ['1', '3', '5', '6'], 'min(9)': ['1', 'b3', '5', '9'], 'maj6(b7)': ['1', '3', '5', '6', 'b7'], '7(#9)': ['1', '3', '5', 'b7', '#9'], 'maj/11': ['11', '1', '3', '5'], 'sus2': ['1', '2', '5'], 'min7/5': ['5', 'b7', '1', '3'], 'min9': ['1', 'b3', '5', 'b7', '9'], 'min/b7': ['b7', '1', 'b3', '5'], 'dim': ['1', 'b3', 'b5'], 'sus4(b7,9)': ['1', '4', '5', 'b7', '9'], 'sus4(b7)': ['1', '4', '5', 'b7'], 'maj13': ['1', '3', '5', '7', '9', '11', '13'], 'sus4': ['1', '4', '5'], 'dim/b5': ['b5', '1', 'b3'], '1': ['1'], 'min/11': ['11', '1', 'b3', '5'], 'sus2(b7)': ['1', '2', '5', 'b7'], 'maj9': ['1', '3', '5', '7', '9'], 'minmaj7': ['1', 'b3', '5', '7'], 'aug(b7)': ['1', '3', '#5', 'b7'], '9': ['1', '3', '5', 'b7', '9'], 'min7/b7': ['b7', '1', 'b3', '5'], 'maj6/3': ['3', '5', '6', '1'], 'maj7/5': ['5', '7', '1', '3'], '13': ['1', '3', '5', 'b7', '9', '11', '13'], 'sus2/9': ['9', '1', '2', '5'], '5/13': ['13', '1', '5'], 'maj/b3': ['b3', '3', '5', '1'], '9(b13)': ['1', '3', '5', 'b7', '9', 'b13'], 'aug': ['1', '3', '#5'], '1(b5,b7,3)/b5': ['b5', 'b7', '1', '3'], 'sus4/5': ['5', '1', '4'], 'min7(11)': ['1', 'b3', '5', 'b7', '11'], 'sus4/11': ['11', '1', '4', '5'], '7/3': ['3', '5', 'b7', '1'], 'min/13': ['13', '1', 'b3', '5'], '9/5': ['5', 'b7', '9', '1', '3'], '9(13,#11)': ['1', '3', '5', 'b7', '9', '13', '#11'], 'min9/9': ['9', '1', 'b3', '5', 'b7'], '1(11,9)': ['1', '11', '9'], 'maj7/9': ['9', '1', '3', '5', '7'], '5(b7)': ['1', '5', 'b7'], 'maj6(b7,11)': ['1', '3', '5', '6', 'b7', '11'], '5(13)': ['1', '5', '13'], 'min7/11': ['11', '1', 'b3', '5', 'b7'], 'maj6(9)': ['9', '1', '3', '5', '6'], 'min11/b3': ['b3', '5', 'b7', '9', '11'], '7(b9)': ['b9', '1', '3', '5', 'b7'], 'dim7/b3': ['b3', 'b5', '6', '1'], '1(b3,b7,11,9)': ['1', 'b3', 'b7', '11', '9'], 'sus4(b7,9,13)': ['1', '4', '5', 'b7', '9', '13'], 'min6/5': ['5', '6', '1', 'b3'], '1(#5)': ['1', '#5'], 'min6': ['1', 'b3', '5', '6'], 'maj6(9)/5': ['5', '6', '9', '1', '3'], 'min9/5': ['5', 'b7', '9', '1', 'b3'], 'min/7': ['7', '1', 'b3', '5'], 'dim7': ['1', 'b3', 'b5', '6'], 'min/b1': ['b1', '1', 'b3', '5'], 'maj6/13': ['13', '1', '3', '5', '6'], 'maj(9)/3': ['3', '5', '9', '1'], 'aug(b7,9)': ['1', '3', '#5', 'b7', '9'], '1(b5,b7,3)': ['1', 'b5', 'b7', '3'], '1(b7)/b7': ['b7', '1'], '1(13)/13': [], '1(3)': [], 'min/3': [], 'maj7/7': [], 'sus4(b7)/9': [], 'hdim7/b3': [], '7/11': [], 'dim/b3': [], 'maj(b9)': [], 'sus4(9)': [], 'maj6(7)': [], '7/b7': [], '7(#11)': [], 'maj(11)': [], 'maj/#11': [], 'hdim7/b7': [], 'min7/b3': [], 'maj(9)/5': [], 'maj/b9': [], 'dim/b9': [], 'min6(7)': [], '7/9': [], '7/13': [], 'maj(11)/11': [], '9(#11)': [], 'maj(#9)': [], 'min11': [], '5(b7)/b7': [], '5(b7)/9': [], '5(b7)/3': [], '9/3': [], '7(b9)/b9': [], 'aug(7)': [], '5(b13)': [], 'min(b13)': [], 'maj7/11': [], 'min6/9': [], 'min/bb7': [], 'maj6/9': [], 'sus4(9)/7': [], 'sus4(b7,9,#11)': [], 'maj(#11)': [], 'min(9)/b7': [], 'min(9)/13': [], 'min/b13': [], 'maj/b11': [], 'sus4/b7': [], 'min11/5': [], 'hdim7/11': [], '7(b13)': [], 'min7(b13)': [], 'min(11)/7': [], 'maj7(#11)': [], 'min13': [], 'maj7/3': [], 'maj6/11': [], 'maj(9)/9': [], 'dim7/9': [], '7(b9,b13)': [], '7(b9)/3': [], 'maj9/3': [], 'min9/b7': [], '7(11)': [], 'sus4(b7)/11': [], '7(b9)/5': [], '7(b9)/b7': [], 'maj7(#11)/3': [], 'dim/b7': [], 'maj/b5': [], '7(b13)/3': [], 'dim(b13)': [], '7(b9,#11)': [], '1(11)': [], '7/b5': [], 'min/9': [], '1(3,7)': [], '5/5': [], '5/b7': [], 'minmaj7/5': [], 'min9/11': [], 'min(9)/5': [], 'min6/b3': [], '1(b3)': [], 'maj6/5': [], '7(b13,#9)': [], '9(13)': [], 'maj9/11': [], '7/b9': [], 'aug/5': [], 'sus4/7': [], 'sus4/9': [], 'min9(b13)': [], 'min(11)/b7': [], 'min(11)/11': [], 'maj9(#11)': [], 'min7/13': [], 'maj6/b5': [], '7/b11': [], 'sus4(b7)/5': [], 'minmaj7/7': [], '5/11': [], 'maj9(13)': [], '7/b3': [], 'maj/b13': [], 'min7/b9': [], 'aug(b7)/3': [], 'min7/9': [], 'sus4(b13,b7)': [], 'hdim7/b5': [], 'min(11,9)': [], '1(3)/3': [], 'aug(9)': [], 'maj/bb13': [], '1(3)/9': [], 'maj6(b9)': [], 'sus2/5': [], 'maj6/b7': [], 'sus4(b7)/b7': [], 'maj7(#5)': [], 'min11/b7': [], '1(b3,b7)/b7': [], 'maj7(#9)': [], 'min(9)/7': [], 'sus4(b7,9)/5': [], 'sus2(#11)': [], '5/9': [], 'maj(9,#11)': [], '1(b7)': []}

pat_maj = r'\Amaj'
pat_min = r'\Amin(?!m)'
pat_dim = r'\Adim'
pat_hdim7 = r'\Ahdim7'
pat_aug = r'\Aaug'
pat_sus = r'\Asus'
pat_minmaj7 = r'\Aminmaj7'
pat_1 = r'\A1(?!1)'
pat_5 = r'\A5'
pat_7 = r'\A7'
pat_9 = r'\A9'
pat_11 = r'\A11'
pat_13 = r'\A13'

bool_maj = False
bool_min = False
bool_dim = False
bool_hdim7 = False
bool_aug = False
bool_sus = False
bool_minmaj7 = False
bool_1 = False
bool_5 = False
bool_7 = False
bool_9 = False
bool_11 = False
bool_13 = False

bool_7_after = False

test_m = re.findall(r'\/(.*)\b', 'Cmin/b5')
print(test_m[0])

unique_chord_types_disassembled = { i : [] for i in unique_chord_types}
for chord_type, assembly in unique_chord_types_disassembled.items():
    this_regex = r''
    these_notes = []
    if re.search(pat_maj, chord_type):
        bool_maj = True
        this_regex = pat_maj
        these_notes = ['1', '3', '5']
    elif re.search(pat_min, chord_type):
        bool_min = True
        this_regex = pat_min
        these_notes = ['1', 'b3', '5']
    elif re.search(pat_dim, chord_type):
        bool_dim = True
        this_regex = pat_dim
        these_notes = ['1', 'b3', 'b5']
    elif re.search(pat_hdim7, chord_type):
        bool_hdim7 = True
        this_regex = pat_hdim7
        these_notes = ['1', 'b3', 'b5', 'b7']
        bool_7_after = True
    elif re.search(pat_aug, chord_type):
        bool_aug = True
        this_regex = pat_aug
        these_notes = ['1', '3', '#5']
    elif re.search(pat_sus, chord_type):
        bool_sus = True
        this_regex = pat_sus
    elif re.search(pat_minmaj7, chord_type):
        bool_minmaj7 = True
        this_regex = pat_minmaj7
        these_notes = ['1', 'b3', '5', '7']
        bool_7_after = True
    elif re.search(pat_1, chord_type):
        bool_1 = True
        this_regex = pat_1
        these_notes = ['1']
    elif re.search(pat_5, chord_type):
        bool_5 = True
        this_regex = pat_5
        these_notes = ['1', '5']
    elif re.search(pat_7, chord_type):
        bool_7 = True
        this_regex = pat_7
        these_notes = ['1', '3', '5', 'b7']
    elif re.search(pat_9, chord_type):
        bool_9 = True
        this_regex = pat_9
        these_notes = ['1', '3', '5', 'b7', '9']
    elif re.search(pat_11, chord_type):
        bool_11 = True
        this_regex = pat_11
        these_notes = ['1', '3', '5', 'b7', '9', '11']
    elif re.search(pat_13, chord_type):
        bool_13 = True
        this_regex = pat_13
        these_notes = ['1', '3', '5', 'b7', '9', '11', '13']
    if (bool_maj | bool_min | bool_dim | bool_aug):
        if re.search(this_regex + r'7', chord_type):
            this_regex += r'7'
            if bool_maj:
                these_notes.append('7')
            elif (bool_min | bool_aug):
                these_notes.append('b7')
            else:
                these_notes.append('bb7')
            bool_7_after = True
    if (bool_maj & (not bool_7_after)):
        if re.search(this_regex + r'6', chord_type):
            this_regex += r'6'
            these_notes.append('6')
        elif re.search(this_regex + r'9', chord_type):
            this_regex += r'9'
            these_notes += ['7', '9']
        elif re.search(this_regex + r'11', chord_type):
            this_regex += r'11'
            these_notes += ['7', '9', '11']
        elif re.search(this_regex + r'13', chord_type):
            this_regex += r'13'
            these_notes += ['7', '9', '11', '13']
    elif (bool_min & (not bool_7_after)):
        if re.search(this_regex + r'6', chord_type):
            this_regex += r'6'
            these_notes.append('6')
        elif re.search(this_regex + r'9', chord_type):
            this_regex += r'9'
            these_notes += ['b7', '9']
        elif re.search(this_regex + r'11', chord_type):
            this_regex += r'11'
            these_notes += ['b7', '9', '11']
        elif re.search(this_regex + r'13', chord_type):
            this_regex += r'13'
            these_notes += ['b7', '9', '11', '13']
    elif bool_sus:
        if re.search(this_regex + r'2', chord_type):
            this_regex += r'2'
            these_notes = ['1', '2', '5']
        elif re.search(this_regex + r'4', chord_type):
            this_regex += r'4'
            these_notes = ['1', '4', '5']
    if re.search(this_regex + r'\(', chord_type):
        this_regex += r'\('
        m = re.findall(r'\((.*)\)', chord_type)
        this_regex += m[0] + r'\)'
        new_notes = m[0].split(",")
        these_notes += new_notes
    if re.search(this_regex + r'\/', chord_type):
        this_regex += r'\/'
        m = re.findall(r'\/(.*)\b', chord_type)
        this_regex += m[0]
        if m[0] in these_notes:
            index = these_notes.index(m[0])
            these_notes = these_notes[index: len(these_notes)] + these_notes[0: index]
        else:
            these_notes_numbers = []
            for note in these_notes:
                num = float(re.findall(r'(\d{1,2})', note)[0])
                if 'bb' in note:
                    these_notes_numbers.append(num - .5)
                elif 'b' in note:
                    these_notes_numbers.append(num - .25)
                elif '#' in note:
                    these_notes_numbers.append(num + .25)
                else:
                    these_notes_numbers.append(num)

                    
                    
            bass_note = re.findall(r'(\d{1,2})', m[0])[0]
            bass_note_num = float(bass_note)
            if 'bb' in m[0]:
                bass_note_num -= .5
            elif 'b' in m[0]:
                bass_note_num -= .25
            elif '#' in m[0]:
                bass_note_num += .25
            
                
            
            index = 0
            
            for note_num in these_notes_numbers:
                if index == len(these_notes_numbers) - 1:
                    these_notes_numbers = [bass_note_num] + these_notes_numbers
                    break
                elif ((bass_note_num > note_num) & ((these_notes_numbers[index + 1] > bass_note_num) | (these_notes_numbers[index + 1] < note_num))):
                    these_notes_numbers = [bass_note_num] + these_notes_numbers[(index + 1): len(these_notes_numbers)] + these_notes_numbers[0: (index + 1)]
                    break
                else:
                    index += 1
            these_notes = []
            for note_num in these_notes_numbers:
                pre_note = str(note_num)
                if re.search(r'\.25', pre_note):
                    num_str = re.findall(r'\A(\d{1,2})\.25', pre_note)[0]
                    these_notes.append('#' + str(int(float(num_str))))
                elif re.search(r'\.5', pre_note):
                    num_str = re.findall(r'\A(\d{1,2})\.5', pre_note)[0]
                    these_notes.append('bb' + str(int(float(num_str)) + 1))
                elif re.search(r'\.75', pre_note):
                    num_str = re.findall(r'\A(\d{1,2})\.75', pre_note)[0]
                    these_notes.append('b' + str(int(float(num_str)) + 1))
                else:
                    these_notes.append(str(int(float(pre_note))))
                
    unique_chord_types_disassembled[chord_type] = these_notes

unique_chord_types_disassembled



b5


{'min': ['1', 'b3', '5'],
 'maj': ['1', '3', '5'],
 'maj/5': ['5', '1', '3'],
 'hdim7': ['1', 'b3', 'b5', 'b7'],
 '7': ['1', '3', '5', 'b7'],
 '7/5': ['5', 'b7', '1', '3'],
 'min/b3': ['b3', '5', '1'],
 'min7': ['1', 'b3', '5', '7'],
 '11': ['1', '3', '5', 'b7', '9', '11'],
 'maj7': ['1', '3', '5', '7'],
 'maj(9)': ['1', '3', '5', '9'],
 '5': ['1', '5'],
 'maj/3': ['3', '5', '1'],
 'maj/7': ['7', '1', '3', '5'],
 'sus2/3': ['3', '5', '1', '2'],
 'maj/9': ['9', '1', '3', '5'],
 'min/5': ['5', '1', 'b3'],
 'min(11)': ['1', 'b3', '5', '11'],
 'maj(11)/b7': ['b7', '11', '1', '3', '5'],
 'maj/b7': ['b7', '1', '3', '5'],
 'maj/13': ['13', '1', '3', '5'],
 'maj6': ['1', '3', '5'],
 'min(9)': ['1', 'b3', '5', '9'],
 'maj6(b7)': ['1', '3', '5'],
 '7(#9)': ['1', '3', '5', 'b7', '#9'],
 'maj/11': ['11', '1', '3', '5'],
 'sus2': ['1', '2', '5'],
 'min7/5': ['5', '7', '1', 'b3'],
 'min9': ['1', 'b3', '5'],
 'min/b7': ['b7', '1', 'b3', '5'],
 'dim': ['1', 'b3', 'b5'],
 'sus4(b7,9)': ['1', '4', '5', 

Still need to work with the parentheses...!!! Not coming through

Also, want the numbers in dict to be ints not 3.0 eg